In [0]:
import requests
from urllib.parse import urlparse
import os
from io import BytesIO
import pyarrow.parquet as pq
import pandas as pd
from pyspark.sql import SparkSession


spark = SparkSession.builder.getOrCreate()


url = "https://d37ci6vzurychx.cloudfront.net/trip-data/yellow_tripdata_2024-01.parquet"


file_name = os.path.basename(urlparse(url).path)
print("File will be called:", file_name)


print("⬇️ Downloading file into memory...")
response = requests.get(url)
response.raise_for_status()  
data_bytes = BytesIO(response.content)


print(" Reading into Pandas DataFrame...")
pandas_df = pq.read_table(data_bytes).to_pandas()
print(" Pandas DataFrame loaded! Shape:", pandas_df.shape)


df = spark.createDataFrame(pandas_df)
print(" Spark DataFrame created!")

display(df.limit(5))  # preview first 5 rows


File will be called: yellow_tripdata_2024-01.parquet
⬇️ Downloading file into memory...
📥 Reading into Pandas DataFrame...
✅ Pandas DataFrame loaded! Shape: (2964624, 19)
✅ Spark DataFrame created!


VendorID tpep_pickup_datetime tpep_dropoff_datetime passenger_count trip_distance RatecodeID store_and_fwd_flag PULocationID DOLocationID payment_type fare_amount extra mta_tax tip_amount tolls_amount improvement_surcharge total_amount congestion_surcharge Airport_fee 2 2024-01-01T00:57:55.000Z 2024-01-01T01:17:43.000Z 1.0 1.72 1.0 N 186 79 2 17.7 1.0 0.5 0.0 0.0 1.0 22.7 2.5 0.0 1 2024-01-01T00:03:00.000Z 2024-01-01T00:09:36.000Z 1.0 1.8 1.0 N 140 236 1 10.0 3.5 0.5 3.75 0.0 1.0 18.75 2.5 0.0 1 2024-01-01T00:17:06.000Z 2024-01-01T00:35:01.000Z 1.0 4.7 1.0 N 236 79 1 23.3 3.5 0.5 3.0 0.0 1.0 31.3 2.5 0.0 1 2024-01-01T00:36:38.000Z 2024-01-01T00:44:56.000Z 1.0 1.4 1.0 N 79 211 1 10.0 3.5 0.5 2.0 0.0 1.0 17.0 2.5 0.0 1 2024-01-01T00:46:51.000Z 2024-01-01T00:52:57.000Z 1.0 0.8 1.0 N 211 148 1 7.9 3.5 0.5 3.2 0.0 1.0 16.1 2.5 0.0

In [0]:
df.columns


['VendorID',
 'tpep_pickup_datetime',
 'tpep_dropoff_datetime',
 'passenger_count',
 'trip_distance',
 'RatecodeID',
 'store_and_fwd_flag',
 'PULocationID',
 'DOLocationID',
 'payment_type',
 'fare_amount',
 'extra',
 'mta_tax',
 'tip_amount',
 'tolls_amount',
 'improvement_surcharge',
 'total_amount',
 'congestion_surcharge',
 'Airport_fee']

In [0]:
pandas_df.write.format("delta").mode("overwrite").saveAsTable(
    "trip_data.trip_source.raw"
)


---------------------------------------------------------------------------
AttributeError                            Traceback (most recent call last)
~/.ipykernel/4291/command-8934655427727657-337580409 in ?()
----> 1 pandas_df.write.format("delta").mode("overwrite").saveAsTable(
      2     "trip_data.trip_source.raw"
      3 )

/databricks/python/lib/python3.12/site-packages/pandas/core/generic.py in ?(self, name)
   6295             and name not in self._accessors
   6296             and self._info_axis._can_hold_identifiers_and_holds_name(name)
   6297         ):
   6298             return self[name]
-> 6299         return object.__getattribute__(self, name)

AttributeError: 'DataFrame' object has no attribute 'write'

In [0]:
df.write.format("delta").mode("overwrite").saveAsTable(
    "trip_data.trip_source.raw"
)



In [0]:
%sql
SELECT * FROM trip_data.trip_source.raw

VendorID tpep_pickup_datetime tpep_dropoff_datetime passenger_count trip_distance RatecodeID store_and_fwd_flag PULocationID DOLocationID payment_type fare_amount extra mta_tax tip_amount tolls_amount improvement_surcharge total_amount congestion_surcharge Airport_fee 2 2024-01-13T19:35:58.000Z 2024-01-13T19:43:42.000Z 2.0 1.05 1.0 N 144 113 1 9.3 0.0 0.5 2.0 0.0 1.0 15.3 2.5 0.0 2 2024-01-13T19:50:51.000Z 2024-01-13T19:57:41.000Z 1.0 0.88 1.0 N 234 170 1 7.9 0.0 0.5 2.38 0.0 1.0 14.28 2.5 0.0 1 2024-01-13T19:15:22.000Z 2024-01-13T19:22:32.000Z 2.0 0.8 1.0 N 114 264 1 7.9 2.5 0.5 2.35 0.0 1.0 14.25 2.5 0.0 1 2024-01-13T19:34:11.000Z 2024-01-13T19:52:22.000Z 2.0 2.6 1.0 N 264 170 1 17.7 2.5 0.5 2.0 0.0 1.0 23.7 2.5 0.0 2 2024-01-13T19:16:13.000Z 2024-01-13T19:33:56.000Z 2.0 3.25 1.0 N 211 33 1 19.1 0.0 0.5 4.62 0.0 1.0 27.72 2.5 0.0 2 2024-01-13T19:43:24.000Z 2024-01-13T20:02:18.000Z 1.0 2.08 1.0 N 137 148 1 17.0 0.0 0.5 4.2 0.0 1.0 25.2 2.5 0.0 2 2024-01-13T19:26:59.000Z 2024-01-13T19:40:51.000Z 1.0 1.1 1.0 N 79 234 1 12.8 0.0 0.5 3.36 0.0 1.0 20.16 2.5 0.0 2 2024-01-13T19:46:45.000Z 2024-01-13T19:56:07.000Z 1.0 0.87 1.0 N 90 107 1 9.3 0.0 0.5 2.66 0.0 1.0 15.96 2.5 0.0 2 2024-01-13T19:12:05.000Z 2024-01-13T19:21:10.000Z 1.0 1.4 1.0 N 140 237 1 10.7 0.0 0.5 2.94 0.0 1.0 17.64 2.5 0.0 2 2024-01-13T19:38:20.000Z 2024-01-13T19:47:32.000Z 1.0 1.94 1.0 N 239 75 1 12.1 0.0 0.5 0.9 0.0 1.0 17.0 2.5 0.0 1 2024-01-13T19:37:40.000Z 2024-01-13T19:49:34.000Z 1.0 1.5 1.0 N 249 231 1 10.7 2.5 0.5 2.95 0.0 1.0 17.65 2.5 0.0 2 2024-01-13T19:10:54.000Z 2024-01-13T19:19:34.000Z 1.0 0.88 1.0 N 229 237 1 9.3 0.0 0.5 2.66 0.0 1.0 15.96 2.5 0.0 2 2024-01-13T19:23:56.000Z 2024-01-13T19:28:22.000Z 1.0 1.01 1.0 N 141 141 1 7.2 0.0 0.5 2.8 0.0 1.0 14.0 2.5 0.0 2 2024-01-13T19:44:22.000Z 2024-01-13T19:53:11.000Z 1.0 1.65 1.0 N 140 162 1 10.7 0.0 0.5 2.94 0.0 1.0 17.64 2.5 0.0 2 2024-01-13T19:20:52.000Z 2024-01-13T19:32:41.000Z 1.0 1.87 1.0 N 79 233 1 12.8 0.0 0.5 2.0 0.0 1.0 18.8 2.5 0.0 2 2024-01-13T19:48:00.000Z 2024-01-13T20:18:53.000Z 1.0 5.29 1.0 N 161 255 1 30.3 0.0 0.5 6.86 0.0 1.0 41.16 2.5 0.0 1 2024-01-13T19:23:18.000Z 2024-01-13T19:33:25.000Z 1.0 1.7 1.0 N 238 142 1 12.1 2.5 0.5 3.2 0.0 1.0 19.3 2.5 0.0 1 2024-01-13T19:43:31.000Z 2024-01-13T19:51:11.000Z 1.0 1.4 1.0 N 142 238 1 10.0 2.5 0.5 1.0 0.0 1.0 15.0 2.5 0.0 2 2024-01-13T19:44:44.000Z 2024-01-13T20:28:09.000Z 1.0 19.31 2.0 N 132 151 1 70.0 0.0 0.5 16.19 6.94 1.0 98.88 2.5 1.75 2 2024-01-13T19:09:25.000Z 2024-01-13T19:23:02.000Z 2.0 1.69 1.0 N 234 229 1 13.5 0.0 0.5 3.5 0.0 1.0 21.0 2.5 0.0 2 2024-01-13T19:27:28.000Z 2024-01-13T19:35:55.000Z 1.0 2.46 1.0 N 237 74 1 12.1 0.0 0.5 4.83 0.0 1.0 20.93 2.5 0.0 2 2024-01-13T19:38:58.000Z 2024-01-13T19:44:31.000Z 1.0 1.37 1.0 N 75 74 2 8.6 0.0 0.5 0.0 0.0 1.0 10.1 0.0 0.0 2 2024-01-13T19:46:09.000Z 2024-01-13T19:53:13.000Z 1.0 1.31 1.0 N 74 42 2 8.6 0.0 0.5 0.0 0.0 1.0 10.1 0.0 0.0 2 2024-01-13T19:20:37.000Z 2024-01-13T19:39:23.000Z 1.0 0.56 1.0 N 164 230 1 15.6 0.0 0.5 0.0 0.0 1.0 19.6 2.5 0.0 2 2024-01-13T19:48:29.000Z 2024-01-13T19:56:34.000Z 1.0 0.81 1.0 N 230 142 1 8.6 0.0 0.5 2.52 0.0 1.0 15.12 2.5 0.0 2 2024-01-13T19:02:13.000Z 2024-01-13T19:02:22.000Z 3.0 0.02 2.0 N 249 249 2 70.0 0.0 0.5 0.0 0.0 1.0 74.0 2.5 0.0 2 2024-01-13T19:02:43.000Z 2024-01-13T19:10:14.000Z 3.0 0.91 1.0 N 249 234 2 8.6 0.0 0.5 0.0 0.0 1.0 12.6 2.5 0.0 2 2024-01-13T19:19:08.000Z 2024-01-13T20:08:05.000Z 1.0 7.15 1.0 N 90 61 2 43.6 0.0 0.5 0.0 0.0 1.0 47.6 2.5 0.0 2 2024-01-13T18:51:42.000Z 2024-01-13T19:08:53.000Z 3.0 2.63 1.0 N 162 246 1 17.7 0.0 0.5 2.0 0.0 1.0 23.7 2.5 0.0 2 2024-01-13T19:01:04.000Z 2024-01-13T19:26:56.000Z 3.0 5.26 1.0 N 233 255 1 28.2 0.0 0.5 1.0 0.0 1.0 33.2 2.5 0.0 1 2024-01-13T19:38:54.000Z 2024-01-13T20:01:18.000Z 2.0 3.7 1.0 N 161 79 1 21.9 2.5 0.5 5.15 0.0 1.0 31.05 2.5 0.0 2 2024-01-13T19:46:28.000Z 2024-01-13T20:18:28.000Z 1.0 9.25 1.0 N 138 230 1 44.3 5.0 0.5 12.05 6.94 1.0 74.04 2.5 1.75 2 2024-01-13T19:25:49.000Z 2024-01-13T19:45:1